In [1]:
import xlsxwriter

In [2]:
from repytex.worksheets.worksheet import pull_datas
from repytex.reports.eval import pull_datas as pull_sqlite
import pandas as pd
import numpy as np
import sqlite3

In [3]:
conn = sqlite3.connect('./recopytex.db')

# to xlxs

In [4]:
datas = pull_datas(1, conn)
datas

{'evaluation':    id               name  term  t_id
 0   1  DS1 mise en jambe     1     1,
 'exercises':    id                        name  eval_id                        date comment
 0   1  1 - Prendre la température        1  2017-09-05 00:00:00.000000        
 1   2             2 - Maladroite!        1  2017-09-05 00:00:00.000000        ,
 'question_scores':       id  question_id  student_id value
 0      1            1           1     1
 1      2            2           1     2
 2      3            3           1     .
 3      4            1           2     2
 4      5            2           2     2
 5      6            3           2     1
 6      7            1           3     3
 7      8            2           3     0
 8      9            3           3     0
 9     10            1           4     3
 10    11            2           4     3
 11    12            3           4     0
 12    13            1           5     1
 13    14            2           5     2
 14    15            

In [5]:
datas['evaluation']["name"][0]

'DS1 mise en jambe'

In [6]:
q_df = datas["questions"]
q_df = q_df.assign(
    Nom = q_df[["name", "comment"]].apply(lambda x: " ".join(x), 1)
)

In [7]:
q_df.head()

id name  score_rate  is_leveled  exercise_id competence       domain  \
0   1    1           0           1            1       Cher    Grandeurs   
1   2    2           0           1            1        Cal    Grandeurs   
2   3  2.c           0           1            1        Cal    Grandeurs   
0   4                0           1            2       Cher  4opérations   
1   5                0           1            2       Cher  4opérations   

                             comment                                    Nom  
0             Lecture du thermomètre               1 Lecture du thermomètre  
1        Suivre programme de calculs          2 Suivre programme de calculs  
2  Renverser un programme de calculs  2.c Renverser un programme de calculs  
0    Lire le tableau et le graphique        Lire le tableau et le graphique  
1             Décomposer le problème                 Décomposer le problème

In [8]:
datas["exercises"]

id                        name  eval_id                        date comment
0   1  1 - Prendre la température        1  2017-09-05 00:00:00.000000        
1   2             2 - Maladroite!        1  2017-09-05 00:00:00.000000

In [9]:
ex_q = q_df.groupby("exercise_id")\
    .agg({"score_rate": np.sum, "competence": lambda x: '-'.join(list(x))}) \
    .merge(datas["exercises"], left_index=True, right_on='id')
ex_q = ex_q.assign(
    Nom = ex_q["name"].apply(lambda x: f"Ex {x}"),
    exercise_id = ex_q["id"]
)
#ex_q

In [10]:
sel_fields = ['Nom', 'competence', 'score_rate', 'exercise_id']
xls_df = pd.concat([ex_q[sel_fields], q_df[sel_fields]]).sort_values("exercise_id")
#xls_df

In [11]:
#writer = pd.ExcelWriter("./test.xlsx", engine="xlsxwriter")
#xls_df.to_excel(writer, index=False, sheet_name='DNB blanc 2')

In [12]:
#workbook = writer.book
#worksheet = writer.sheets['DNB blanc 2']

In [13]:
#first_line_format = workbook.add_format({"align": 'center', "rotation":90})

#worksheet.set_column('A:D', 20)


In [14]:
#writer.save()

## From xlsx

In [15]:
df = pd.read_excel("./DNB_blanc2/DNB2_306.xlsx")
df.head()

competence  Barème  A. Rachma  A. kassim  \
DNB blanc 2                      NaN     116         51         10   
Ex 1 - Le fameux triangle        NaN      10          5          0   
1 Reconnaitre Pythagore          Mod       3          3          0   
1 Calculs                        Cal       3          2          0   
2 Calcul de l'aire               Rep       4          0          0   

                           A. Irchadi  A. Mikidadi  A. Zaidou  B. Rakchat  \
DNB blanc 2                        63           53         27          17   
Ex 1 - Le fameux triangle          10            9          3           0   
1 Reconnaitre Pythagore             3            3          1           0   
1 Calculs                           3            3          2           0   
2 Calcul de l'aire                  4            3          0           0   

                           B. Chadia  C. Faycoil  ...   S. Nadjoi  S. Rachida  \
DNB blanc 2                       32          26  ...          49          28   
Ex 1 - Le fameux triangle          5           0  ...           7           6   
1 Reconnaitre Pythagore            3           0  ...           3           3   
1 Calculs                          2           0  ...           3           3   
2 Calcul de l'aire                 0           0  ...           1           0   

                           S. Hairidine  T. Zoubert    Moyenne   Min    Q1  \
DNB blanc 2                          12          10  35.952381  10.0  25.0   
Ex 1 - Le fameux triangle             0           0   3.857143   0.0   0.0   
1 Reconnaitre Pythagore               0           0   1.571429   0.0   0.0   
1 Calculs                             0           0   1.428571   0.0   0.0   
2 Calcul de l'aire                    0           0   0.857143   0.0   0.0   

                             me    Q3   max  
DNB blanc 2                32.0  51.0  70.0  
Ex 1 - Le fameux triangle   3.0   7.0  10.0  
1 Reconnaitre Pythagore     2.0   3.0   3.0  
1 Calculs                   2.0   3.0   3.0  
2 Calcul de l'aire          0.0   1.0   4.0  

[5 rows x 29 columns]

On enlève les colonnes inutiles et on format les prénoms

In [16]:
import unicodedata
def normalize_str(s):
    return unicodedata.normalize('NFD', s).encode('ascii', 'ignore').lower()

In [17]:
df = df.drop(['competence', 'Barème','Moyenne',
       'Min', 'Q1', 'me', 'Q3', 'max'], 1)
df.columns = [normalize_str(i.split(". ")[-1]) for i in df.columns]
df.head()

b'rachma'  b'kassim'  b'irchadi'  b'mikidadi'  \
DNB blanc 2                       51         10          63           53   
Ex 1 - Le fameux triangle          5          0          10            9   
1 Reconnaitre Pythagore            3          0           3            3   
1 Calculs                          2          0           3            3   
2 Calcul de l'aire                 0          0           4            3   

                           b'zaidou'  b'rakchat'  b'chadia'  b'faycoil'  \
DNB blanc 2                       27          17         32          26   
Ex 1 - Le fameux triangle          3           0          5           0   
1 Reconnaitre Pythagore            1           0          3           0   
1 Calculs                          2           0          2           0   
2 Calcul de l'aire                 0           0          0           0   

                           b'djael'  b'doulka-rynaini'     ...      \
DNB blanc 2                      39                 27     ...       
Ex 1 - Le fameux triangle         1                  0     ...       
1 Reconnaitre Pythagore           0                  0     ...       
1 Calculs                         0                  0     ...       
2 Calcul de l'aire                1                  0     ...       

                           b'chamsidine'  b'dania'  b'issoufi'  b'el-fahar'  \
DNB blanc 2                           33        67          70           59   
Ex 1 - Le fameux triangle              3         9           8            8   
1 Reconnaitre Pythagore                2         3           3            3   
1 Calculs                              1         2           3            3   
2 Calcul de l'aire                     0         4           2            2   

                           b'fayadhui'  b'dalila'  b'nadjoi'  b'rachida'  \
DNB blanc 2                         10         47         49          28   
Ex 1 - Le fameux triangle            0          7          7           6   
1 Reconnaitre Pythagore              0          3          3           3   
1 Calculs                            0          3          3           3   
2 Calcul de l'aire                   0          1          1           0   

                           b'hairidine'  b'zoubert'  
DNB blanc 2                          12          10  
Ex 1 - Le fameux triangle             0           0  
1 Reconnaitre Pythagore               0           0  
1 Calculs                             0           0  
2 Calcul de l'aire                    0           0  

[5 rows x 21 columns]

On enlèves les lignes calculées par excel pour ne garder que les données

In [18]:
df = df[list(~df.reset_index()["index"].apply(lambda x: x.startswith("Ex") or x.startswith("DNB")))]
df.head()

b'rachma'  b'kassim'  b'irchadi'  b'mikidadi'  \
1 Reconnaitre Pythagore           3          0           3            3   
1 Calculs                         2          0           3            3   
2 Calcul de l'aire                0          0           4            3   
3 Commentaire de Tristan          1          0           2            2   
1.a Lecture de tableau            3          0           3            3   

                          b'zaidou'  b'rakchat'  b'chadia'  b'faycoil'  \
1 Reconnaitre Pythagore           1           0          3           0   
1 Calculs                         2           0          2           0   
2 Calcul de l'aire                0           0          0           0   
3 Commentaire de Tristan          0           0          0           0   
1.a Lecture de tableau            3           3          3           3   

                          b'djael'  b'doulka-rynaini'     ...      \
1 Reconnaitre Pythagore          0                  0     ...       
1 Calculs                        0                  0     ...       
2 Calcul de l'aire               1                  0     ...       
3 Commentaire de Tristan         3                  0     ...       
1.a Lecture de tableau           3                  0     ...       

                          b'chamsidine'  b'dania'  b'issoufi'  b'el-fahar'  \
1 Reconnaitre Pythagore               2         3           3            3   
1 Calculs                             1         2           3            3   
2 Calcul de l'aire                    0         4           2            2   
3 Commentaire de Tristan              1         2           1            0   
1.a Lecture de tableau                3         3           3            3   

                          b'fayadhui'  b'dalila'  b'nadjoi'  b'rachida'  \
1 Reconnaitre Pythagore             0          3          3           3   
1 Calculs                           0          3          3           3   
2 Calcul de l'aire                  0          1          1           0   
3 Commentaire de Tristan            0          1          0           0   
1.a Lecture de tableau              0          3          3           3   

                          b'hairidine'  b'zoubert'  
1 Reconnaitre Pythagore              0           0  
1 Calculs                            0           0  
2 Calcul de l'aire                   0           0  
3 Commentaire de Tristan             0           0  
1.a Lecture de tableau               0           0  

[5 rows x 21 columns]

In [19]:
df = df.reset_index()
df.head()

index  b'rachma'  b'kassim'  b'irchadi'  b'mikidadi'  \
0   1 Reconnaitre Pythagore          3          0           3            3   
1                 1 Calculs          2          0           3            3   
2        2 Calcul de l'aire          0          0           4            3   
3  3 Commentaire de Tristan          1          0           2            2   
4    1.a Lecture de tableau          3          0           3            3   

   b'zaidou'  b'rakchat'  b'chadia'  b'faycoil'  b'djael'     ...      \
0          1           0          3           0         0     ...       
1          2           0          2           0         0     ...       
2          0           0          0           0         1     ...       
3          0           0          0           0         3     ...       
4          3           3          3           3         3     ...       

   b'chamsidine'  b'dania'  b'issoufi'  b'el-fahar'  b'fayadhui'  b'dalila'  \
0              2         3           3            3            0          3   
1              1         2           3            3            0          3   
2              0         4           2            2            0          1   
3              1         2           1            0            0          1   
4              3         3           3            3            0          3   

   b'nadjoi'  b'rachida'  b'hairidine'  b'zoubert'  
0          3           3             0           0  
1          3           3             0           0  
2          1           0             0           0  
3          0           0             0           0  
4          3           3             0           0  

[5 rows x 22 columns]

In [20]:
df = df.assign(
    q_name = df["index"].apply(lambda x: x.split(" ")[0]),
    q_comment = df["index"].apply(lambda x: " ".join(x.split(" ")[1:])),
        )
df.head()

index  b'rachma'  b'kassim'  b'irchadi'  b'mikidadi'  \
0   1 Reconnaitre Pythagore          3          0           3            3   
1                 1 Calculs          2          0           3            3   
2        2 Calcul de l'aire          0          0           4            3   
3  3 Commentaire de Tristan          1          0           2            2   
4    1.a Lecture de tableau          3          0           3            3   

   b'zaidou'  b'rakchat'  b'chadia'  b'faycoil'  b'djael'   ...    b'issoufi'  \
0          1           0          3           0         0   ...             3   
1          2           0          2           0         0   ...             3   
2          0           0          0           0         1   ...             2   
3          0           0          0           0         3   ...             1   
4          3           3          3           3         3   ...             3   

   b'el-fahar'  b'fayadhui'  b'dalila'  b'nadjoi'  b'rachida'  b'hairidine'  \
0            3            0          3          3           3             0   
1            3            0          3          3           3             0   
2            2            0          1          1           0             0   
3            0            0          1          0           0             0   
4            3            0          3          3           3             0   

   b'zoubert'               q_comment  q_name  
0           0   Reconnaitre Pythagore       1  
1           0                 Calculs       1  
2           0        Calcul de l'aire       2  
3           0  Commentaire de Tristan       3  
4           0      Lecture de tableau     1.a  

[5 rows x 24 columns]

In [21]:
df = df.set_index(["index", "q_name", "q_comment"]).stack().reset_index()
df.head()

index q_name              q_comment      level_3  0
0  1 Reconnaitre Pythagore      1  Reconnaitre Pythagore    b'rachma'  3
1  1 Reconnaitre Pythagore      1  Reconnaitre Pythagore    b'kassim'  0
2  1 Reconnaitre Pythagore      1  Reconnaitre Pythagore   b'irchadi'  3
3  1 Reconnaitre Pythagore      1  Reconnaitre Pythagore  b'mikidadi'  3
4  1 Reconnaitre Pythagore      1  Reconnaitre Pythagore    b'zaidou'  1

In [22]:
df = df.rename(columns={0:"value", "level_3": "norm_surname"})

Il ne reste plus qu'à trouver les correspondances avec la base de données.

In [23]:
sqlite_datas = pull_sqlite(33, conn)

Les élèves

In [24]:
st_df = sqlite_datas["students"]
st_df = st_df.assign(
    norm_surname = st_df["surname"].apply(normalize_str)
)
st_df.head()

id      name   surname mail commment  tribe_id norm_surname
0  27  ABDALLAH    Rachma          None         2    b'rachma'
1  28     ABDOU    Kassim          None         2    b'kassim'
2  29   AHAMADI   Irchadi          None         2   b'irchadi'
3  30    AHAMED  Mikidadi          None         2  b'mikidadi'
4  31      ANLI  El Anziz          None         2  b'el anziz'

In [25]:
df = pd.merge(df, st_df, left_on='norm_surname', right_on="norm_surname")[["q_comment", "id", "value"]]

Les questions

In [26]:
q_df = sqlite_datas["questions"]
q_df.head()

id        name  score_rate  is_leveled  exercise_id competence  \
0  369           1           3           0          114        Mod   
1  370           1           3           0          114        Cal   
2  371           2           4           0          114        Rep   
0  372         1.a           3           0          115       Cher   
1  373  1.b et 2.b           3           0          115        Rep   

         domain                comment  
0     Geometrie  Reconnaitre Pythagore  
1     Geometrie                Calculs  
2     Geometrie       Calcul de l'aire  
0  Statistiques     Lecture de tableau  
1  Statistiques     Minimum et maximum

In [27]:
df = pd.merge(df, q_df, left_on="q_comment", right_on="comment")[["id_x", "id_y", "value"]]\
    .rename(columns={"id_x": "student_id", "id_y": "question_id"})

Yes ça y est je dois les avoir!

In [28]:
df.head()

student_id  question_id  value
0          27          369      3
1          28          369      0
2          29          369      3
3          30          369      3
4          32          369      1

Et maintenant on sauvegarde tout!

In [29]:
df.to_sql("score", conn, if_exists='append', index=False)

In [30]:
fdsqfdsq

NameError: name 'fdsqfdsq' is not defined

## Fait au DNB blanc 1

In [ ]:
wb = xlsxwriter.Workbook("DNB_BLANC_pro1.xlsx")

Formatages

In [ ]:
eval_format = wb.add_format({'bold': True, 'font_color': 'red'})
eval_cell = wb.add_format()
eval_cell.set_bg_color("red")
# exo_cell

La feuille de calcul

In [ ]:
wb = xlsxwriter.Workbook("DS4_302.xlsx")

In [ ]:
ws = wb.add_worksheet()

En tête du tableau

In [ ]:
ws.write(0,1,"Competence")
ws.write(0,2,"Barème")

Toutes les questions et exercices

In [ ]:
def q_line(q, row, ws):
    ws.write(row, 0, f"{q.name} - {q.comment}")
    ws.write(row, 1, f"{q.competence}")
    ws.write(row, 2, q.score_rate)

In [ ]:
def exo_block(exo, row, ws):
    qrow = row
    for q in exo["questions"]:
        qrow += 1
        q_line(q, qrow, ws)
    ws.write(row, 0, f"Ex {exo['name']}")
    row_range = ", ".join([f"C{i}" for i in range(row+2, qrow+2)])
    for i in range(30):
        ws.write(row, i+2, f"=SUM({row_range})")
    return qrow

In [ ]:
row = 2
exo_rows = []
for exo in ev.exercises:
    exo_rows.append(row)
    row = exo_block(exo, row, ws) + 1
ws.write(1,0, ev.name, eval_format)
exo_xls_range = ", ".join([f"C{i+1}" for i in exo_rows])
for i in range(30):
    ws.write(1,i+2, f"=SUM({exo_xls_range})", eval_format)

In [ ]:
wb.close()

# Avec openpyxl

In [ ]:
from openpyxl import Workbook
from openpyxl.styles import PatternFill, Border, Side, Alignment, Protection, Font, colors

In [ ]:
colors.RED

In [ ]:
wb = Workbook()

In [ ]:
ws = wb.create_sheet(ev.name)

In [ ]:
ws.cell(1,2,"Competence")
ws.cell(1,3,"Barème")

In [ ]:
def q_line(q, row, ws):
    ws.cell(row, 1, f"{q.name} - {q.comment}")
    ws.cell(row, 2, f"{q.competence}")
    ws.cell(row, 3, q.score_rate)

In [ ]:
def exo_block(exo, row, ws):
    qrow = row
    for q in exo["questions"]:
        qrow += 1
        q_line(q, qrow, ws)
    ws.cell(row, 1, f"Ex {exo['name']}")
    row_range = ", ".join([f"C{i}" for i in range(row+1, qrow+1)])
    ws.cell(row, 3, f"=SUM({row_range})")
    return qrow

In [ ]:
row = 3
exo_rows = []
for exo in ev.exercises:
    exo_rows.append(row)
    row = exo_block(exo, row, ws) + 1
eval_row = ws.row_dimensions[2]
eval_row.fill = PatternFill(bgColor=colors.RED)
ws.cell(2,1, ev.name)
exo_xls_range = ", ".join([f"C{i}" for i in exo_rows])
ws.cell(2,3, f"=SUM({exo_xls_range})")

In [ ]:
ev.tribe

In [ ]:
wb.save(f"./{ev.name}-{ev.tribe}.xlsx")